DRIVE


In [2]:
from google.colab import drive
drive.mount('/content/drive/')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


OPEN3D


In [3]:
!pip install Open3D

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 399.7/399.7 MB 2.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.5/7.5 MB 20.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.4/139.4 kB 6.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 37.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 38.5 MB/s eta 0:00:00
  Attempting uninstall: widgetsnbextension
    Found existing installation: widgetsnbextension 3.6.7
    Uninstalling widgetsnbextension-3.6.7:
      Successfully uninstalled widgetsnbextension-3.6.7
  Attempting uninstall: ipywidgets
    Found existing installation: ipywidgets 7.7.1
    Uninstalling ipywidgets-7.7.1:
      Successfully uninstalled ipywidgets-7.7.1


Initialization

In [4]:
 !mkdir -p /data/sets/nuscenes  # Make the directory to store the nuScenes dataset in.

 !wget https://www.nuscenes.org/data/v1.0-mini.tgz  # Download the nuScenes mini split.

 !tar -xf v1.0-mini.tgz -C /data/sets/nuscenes  # Uncompress the nuScenes mini split.

 !pip install nuscenes-devkit &> /dev/null  # Install nuScenes.

--2024-07-29 13:01:44--  https://www.nuscenes.org/data/v1.0-mini.tgz
Resolving www.nuscenes.org (www.nuscenes.org)... 3.162.112.13, 3.162.112.92, 3.162.112.127, ...
Connecting to www.nuscenes.org (www.nuscenes.org)|3.162.112.13|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4167696325 (3.9G) [application/x-tar]
Saving to: ‘v1.0-mini.tgz’

v1.0-mini.tgz       100%[===================>]   3.88G   106MB/s    in 34s     

2024-07-29 13:02:18 (117 MB/s) - ‘v1.0-mini.tgz’ saved [4167696325/4167696325]



In [5]:
%matplotlib inline

from nuscenes.nuscenes import NuScenes

nusc = NuScenes(version='v1.0-mini', dataroot='/data/sets/nuscenes', verbose=True)

Loading NuScenes tables for version v1.0-mini...
23 category,
8 attribute,
4 visibility,
911 instance,
12 sensor,
120 calibrated_sensor,
31206 ego_pose,
8 log,
10 scene,
404 sample,
31206 sample_data,
18538 sample_annotation,
4 map,
Done loading in 1.124 seconds.
Reverse indexing ...
Done reverse indexing in 0.2 seconds.


IMPORTATIONS

In [6]:
import open3d as o3d
import numpy as np
import os
import matplotlib.pyplot as plt
import plotly.graph_objects as go

CODE ON ALL DATASET

In [10]:
def interneship (directory):
  for my_sample in nusc.sample:
    #nusc.render_sample_data(my_sample['data']['LIDAR_TOP'])
    LIDAR_TOP_data = nusc.get('sample_data', my_sample['data']['LIDAR_TOP']['filename'])
    CAM_FRONT_data = nusc.get('sample_data', my_sample['data']['CAM_FRONT']['filename'])
    CAM_BACK_data = nusc.get('sample_data', my_sample['data']['CAM_BACK']['filename'])
    CAM_FRONT_LEFT_data = nusc.get('sample_data', my_sample['data']['CAM_FRONT_LEFT']['filename'])
    CAM_FRONT_RIGHT_data = nusc.get('sample_data', my_sample['data']['CAM_FRONT_RIGHT']['filename'])
    lidar_point_cloud(directory, LIDAR_TOP_data,output_folder)



LIDAR_POINT_CLOUD (TOTALE CODE) :

In [81]:

def lidar_point_cloud(directory,filename,output_folder):
  #get the file
  pcd = get_point_cloud(directory,filename)
  o3d_pcd = voxalisation(pcd)
  #filtre the point cloud
  filtred_PCL = filter(o3d_pcd)
  #ransac
  outliers,inliers =ransac(filtred_PCL, distance_threshold=0.5, ransac_n=3, num_iterations=1000)
  #bdscan
  outliers_db =dbscan(outliers, eps=1.0, min_points=10)
#visualisation
  #fig0 = plotly_fig(outliers)
  #fig1 = plotly_fig(inliers)
  fig2 = visualize_point_clouds(outliers, show=True, save=False, output_folder=output_folder, filename=filename)
  fig3 = visualize_point_clouds(inliers, show=True, save=False, output_folder=output_folder, filename=filename)
  fig4 = visualize_point_clouds(inliers,outliers, show=True, save=False, output_folder=output_folder, filename=filename)

  return fig2,fig3,fig4





LOAD AND CONVERT POINT CLOUD

In [7]:
def get_point_cloud(directory,filname):
  # Load binary point cloud
  bin_pcd = np.fromfile(os.path.join(directory, filname), dtype=np.float32)
  points = bin_pcd.reshape((-1, 4))[:, 0:3]

  # Convert to Open3D point cloud
  pcd = o3d.geometry.PointCloud(o3d.utility.Vector3dVector(points))
  return pcd


VOXALISATION

In [67]:
def voxalisation (pcd):
  print("Number of points BEFORE: ", len(pcd.points))
  o3d_pcd= pcd.voxel_down_sample(voxel_size=0.0001)
  print("Number of points AFTER: ", len(o3d_pcd.points))
  o3d.visualization.draw_geometries([o3d_pcd])
  return o3d_pcd

FILTER

In [55]:
def filter (o3d_pcd):
  # Filter points
  filtered_points = [point for point in o3d_pcd.points if point[2] < 50  ] #and point[1] < 230 and point[1] > -80 and point[0] < 250  and point[0] > -70

  # Convert to Open3D point cloud
  filtred_PCL = o3d.geometry.PointCloud(o3d.utility.Vector3dVector(filtered_points))

  # Visualize the filtered point cloud
  o3d.visualization.draw_geometries([filtred_PCL])

  #points before and after filter
  print("Number of points BEFORE: ", len(o3d_pcd.points))
  print("Number of points AFTER: ", len(filtred_PCL.points))

  return filtred_PCL


RANSAC

In [77]:
def ransac(point_cloud, distance_threshold=0.5, ransac_n=3, num_iterations=1000):
    """
    RANSAC-based plane segmentation for a point cloud.
    Parameters:
        point_cloud (open3d.geometry.PointCloud): The input point cloud.
        distance_threshold (float, optional): The maximum distance a point can be from the plane to be considered an inlier.
            Default is 0.1.
        ransac_n (int, optional): The number of points to randomly sample for each iteration of RANSAC. Default is 3.
        num_iterations (int, optional): The number of RANSAC iterations to perform. Default is 1000.
    Returns:
        open3d.geometry.PointCloud, open3d.geometry.PointCloud: Two point clouds representing the inliers and outliers
        of the segmented plane, respectively.
    """
    # Perform plane segmentation using RANSAC
    plane_model, inliers = point_cloud.segment_plane(distance_threshold=distance_threshold, ransac_n=ransac_n,
                                                    num_iterations=num_iterations)

    # Extract inlier and outlier point clouds
    inlier_cloud = point_cloud.select_by_index(inliers)
    outlier_cloud = point_cloud.select_by_index(inliers, invert=True)

    # Color the outlier cloud red and the inlier cloud blue
    outlier_cloud.paint_uniform_color([0.8, 0.2, 0.2])  # Red
    inlier_cloud.paint_uniform_color([0.25, 0.5, 0.75])  # Blue
    return outlier_cloud, inlier_cloud

PLOTLY_DISTANCE : 3D REPRESETATION DE POINT CLOUD % A L'ORIGINE



In [13]:
def plotly_distance(points, show=True):
    # Calculate distances from the origin
    distances = np.linalg.norm(points, axis=1)

    # Create the 3D scatter plot
    fig = go.Figure(data=[go.Scatter3d(
        x=points[:, 0],
        y=points[:, 1],
        z=points[:, 2],
        mode='markers',
        marker=dict(
            size=2,
            color=distances,  # use distances for color
            colorscale='Inferno',  # choose a colorscale
            colorbar=dict(title="Distance from Origin"),  # add a colorbar title
            opacity=0.8
        )
    )])
    fig.update_scenes(aspectmode='data')

    if show == True:
        fig.show()

DBSCAN : CLUSTRING

In [14]:
def dbscan(outlier_cloud, eps=1.0, min_points=10):
    """
    Perform Density-Based Spatial Clustering of Applications with Noise (DBSCAN) on the input point cloud.

    Parameters:
        outlier_cloud (open3d.geometry.PointCloud): The input point cloud to be clustered.
        eps (float, optional): The maximum distance between two points for one to be considered as in the neighborhood of the other.
            Default is 1.0.
        min_points (int, optional): The minimum number of points required to form a dense region (core points). Default is 10.

    Returns:
        open3d.geometry.PointCloud: The input point cloud with updated cluster colors.
        numpy.ndarray: Array of cluster labels assigned to each point in the point cloud.
    """

    # Perform DBSCAN clustering on the input point cloud
    labels = np.array(outlier_cloud.cluster_dbscan(eps=eps, min_points=min_points, print_progress=True))

    # Find the maximum cluster label to get the total number of clusters
    max_label = labels.max()
    print(f"\nPoint cloud has {max_label + 1} clusters")

    # Generate colors for the clusters using a colormap
    colors = plt.get_cmap("hsv")(labels / (max_label if max_label > 0 else 1))
    colors[labels < 0] = 0

    # Assign the computed colors to the point cloud
    outlier_cloud.colors = o3d.utility.Vector3dVector(colors[:, :3])

    # Return the point cloud with updated colors and the cluster labels
    return outlier_cloud, labels

PLOTLY_FIG :

In [15]:
def plotly_fig(point_cloud):
        # Extract the point cloud's coordinates as a numpy array
        points = np.asarray(point_cloud.points)

        # Check if the point cloud has color information
        if hasattr(point_cloud, 'colors') and len(point_cloud.colors) == len(point_cloud.points):
            colors = np.asarray(point_cloud.colors)
        else:
            colors = np.zeros((len(point_cloud.points), 3))  # Default to black color if no colors provided

        fig = go.Figure(data=[go.Scatter3d(
            x=points[:, 0],
            y=points[:, 1],
            z=points[:, 2],
            mode='markers',
            marker=dict(
                size=2,
                color=colors,
                opacity=0.8
            )
        )])

        # Update the scene layout if needed
        fig.update_layout(
            scene=dict(
                xaxis=dict(visible=False, range=[-70, 70]),
                yaxis=dict(visible=False, range=[-40, 40]),
                zaxis=dict(visible=False, range=[-5, 1]),
                aspectmode='manual', aspectratio=dict(x=2, y=1, z=0.1),
                camera=dict(
                    up=dict(x=0.15, y=0, z=1),
                    center=dict(x=0, y=0, z=0.1),
                    eye=dict(x=-0.3, y=0, z=0.2)
                )
            ),
            # plot_bgcolor='black',  # background
            # paper_bgcolor='black',  # background
            scene_dragmode='orbit'
        )

        return fig

VISUALIZE_POINT_CLOUDS : Visualize one or more 3D point clouds and optionally save the plot as an image

In [20]:

def visualize_point_clouds(*point_clouds, show=True, save=False, output_folder='output', filename='new_lidar_point_could_file'):
    """

    Parameters:
        *point_clouds: Variable-length arguments, each representing a 3D point cloud data.
                       Can be numpy.ndarray or open3d.geometry.PointCloud.
        show (bool, optional): If True, the plot will be displayed interactively. Default is True.

    Returns:
        plotly.graph_objects.Figure: The Plotly figure object.
    """
    fig_combined = go.Figure()

    for pc in point_clouds:
        # Convert input to Open3D PointCloud if provided as a numpy array
        if isinstance(pc, np.ndarray):
            pc = o3d.geometry.PointCloud(o3d.utility.Vector3dVector(pc))

        # Call get_plotly_fig to get the Plotly figure for the current point cloud
        fig = plotly_fig(pc)

        # Add the trace from the current figure to the combined figure
        fig_combined.add_trace(fig.data[0])

    # Update the layout if needed (common for all point clouds)
    fig_combined.update_layout(fig.layout)

    if show:
        fig_combined.show()

    # Save the plot as an image if save is True
    if save:
      output_bin_file_path = os.path.join(output_folder, filename)
      points.astype(np.float32).tofile(output_bin_file_path)
      print(f"All points saved as binary file: {output_bin_file_path}")




    return fig_combined

TEST


In [ ]:
lidar_point_cloud("/content/drive/MyDrive/stage_actia/LIDAR_TOP","n008-2018-08-27-11-48-51-0400__LIDAR_TOP__1535385096900138.pcd.bin","/content/drive/MyDrive/stage_actia/LIDAR_TOP_MODIFIED")

Number of points BEFORE:  43440
Number of points AFTER:  40798
[Open3D WARNING] GLFW Error: X11: The DISPLAY environment variable is missing
[Open3D WARNING] Failed to initialize GLFW
[Open3D WARNING] [DrawGeometries] Failed creating OpenGL window.
[Open3D WARNING] GLFW Error: X11: The DISPLAY environment variable is missing
[Open3D WARNING] Failed to initialize GLFW
[Open3D WARNING] [DrawGeometries] Failed creating OpenGL window.
Number of points BEFORE:  40798
Number of points AFTER:  40481

Point cloud has 535 clusters


In [44]:
outliers, inliers = ransac(filtred_PCL, distance_threshold=0.1, ransac_n=3, num_iterations=10000)

# Visualize the segmented plane and outliers
o3d.visualization.draw_geometries([inliers,outliers], point_show_normal=True)

NameError: name 'filtred_PCL' is not defined

TEST : COLORATION DE POIONT CLOUD SELON LA DISTACE % L'ORIGINE

In [19]:
plotly_distance(points, show=True)

NameError: name 'points' is not defined

Test : dbscan

In [ ]:
dbscan(outliers, eps=1.0, min_points=10)


Point cloud has 94 clusters


(PointCloud with 66877 points.,
 array([ 0,  0,  1, ..., 35,  4, 35], dtype=int32))

In [ ]:
fig0,fig1,fig2,fig3 = lidar_point_cloud("/content/drive/MyDrive/stage_actia/LIDAR_TOP","n008-2018-08-01-15-16-36-0400__LIDAR_TOP__1533151622948227.pcd.bin")

Number of points BEFORE:  43400
Number of points AFTER:  33579
[Open3D WARNING] GLFW Error: X11: The DISPLAY environment variable is missing
[Open3D WARNING] Failed to initialize GLFW
[Open3D WARNING] [DrawGeometries] Failed creating OpenGL window.
[Open3D WARNING] GLFW Error: X11: The DISPLAY environment variable is missing
[Open3D WARNING] Failed to initialize GLFW
[Open3D WARNING] [DrawGeometries] Failed creating OpenGL window.
Number of points BEFORE:  33579
Number of points AFTER:  32841

Point cloud has 404 clusters


In [ ]:
fig0

In [ ]:
fig2

In [ ]:
fig1

In [ ]:
fig3